# Rendering Gaussian Splats using `gsplat`

In this notebook, I provide a description on how to load and render gaussian splats files inside a Jupyter notebook. Follow the instructions for proper functioning.

# Dependencies Installation

In [33]:
!pip install -q gsplat mediapy plyfile torch torchvision torchaudio

In [34]:
import torch
import numpy as np
from plyfile import PlyData
import mediapy as media
import os

I already pre-compiled the CUDA binaries for T4 GPU (Google Colab). You can omit the next $3$ steps if you would like to compile from scratch (takes around $15$ minutes).

In [35]:
!git clone https://github.com/DavidVista/SplatsRenderer

fatal: destination path 'SplatsRenderer' already exists and is not an empty directory.


In [36]:
import shutil

shutil.unpack_archive("/content/SplatsRenderer/cuda_files.zip", "/content/")

In [37]:
import os
os.environ["TORCH_CUDA_ARCH_LIST"] = "7.5"  # for T4 GPU in Colab

# restore cache
!mkdir -p ~/.cache/torch_extensions
!cp -r /content/py312_cu126/ ~/.cache/torch_extensions/
print("Restored compiled CUDA extensions from Drive.")

Restored compiled CUDA extensions from Drive.


In [38]:
device = "cuda" if torch.cuda.is_available() else "cpu"
print("Using device:", device)

Using device: cuda


Now, let's download sample point cloud files with gaussian splats (`.ply` files):

In [39]:
import gdown, zipfile, os

file_id = '1Fd04T_sPGkozim08N72jZaaObANXx5-A'
extract_folder = '/content/scenes'
os.makedirs(extract_folder, exist_ok=True)

zip_path = '/content/temp.zip'
gdown.download(f'https://drive.google.com/uc?id={file_id}', zip_path, quiet=False)

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_folder)
    print(f"Extracted {len(zip_ref.namelist())} items")

print("Ready to use! Files are in:", extract_folder)

Downloading...
From (original): https://drive.google.com/uc?id=1Fd04T_sPGkozim08N72jZaaObANXx5-A
From (redirected): https://drive.google.com/uc?id=1Fd04T_sPGkozim08N72jZaaObANXx5-A&confirm=t&uuid=b8b9a9c1-c80b-4470-8569-8fad07ea56ec
To: /content/temp.zip
100%|██████████| 478M/478M [00:07<00:00, 68.0MB/s]


Extracted 2 items
Ready to use! Files are in: /content/scenes


In [40]:
PLY_PATH = "/content/scenes/museume.ply"
assert os.path.exists(PLY_PATH), "Upload your .ply file to Colab first."

# Load `.ply` files

Now we load point cloud information into the main memory:


In [41]:
def load_gaussian_ply(path):
    plydata = PlyData.read(path)
    data = plydata.elements[0].data

    means = np.stack([data['x'], data['y'], data['z']], axis=1)
    colors = np.stack([data['f_dc_0'], data['f_dc_1'], data['f_dc_2']], axis=1)
    opacities = np.array(data['opacity'])
    scales = np.stack([data['scale_0'], data['scale_1'], data['scale_2']], axis=1)
    quats = np.stack([data['rot_0'], data['rot_1'], data['rot_2'], data['rot_3']], axis=1)

    return {
        "means": torch.tensor(means, dtype=torch.float32, device=device),
        "colors": torch.sigmoid(torch.tensor(colors, dtype=torch.float32, device=device)),
        "opacities": torch.sigmoid(torch.tensor(opacities, dtype=torch.float32, device=device)),
        "scales": torch.exp(torch.tensor(scales, dtype=torch.float32, device=device)),
        "quats": torch.tensor(quats, dtype=torch.float32, device=device),
    }

gaussians = load_gaussian_ply(PLY_PATH)
print("Loaded", len(gaussians["means"]), "Gaussians")

Loaded 7389888 Gaussians


# Rendering Functions

## Basic rendering

To render a scene, we need to define the camera instrinsics information and basic operations. I further present some other methods for moving camera.

In [42]:
from gsplat import rasterization

def make_K(width, height, fov=60.0):
    """Return [3,3] pinhole camera intrinsics matrix."""
    f = 0.5 * width / np.tan(0.5 * np.radians(fov))
    K = torch.tensor([[f, 0, width / 2],
                      [0, f, height / 2],
                      [0, 0, 1]], dtype=torch.float32, device=device)
    return K

def pose_from_xyzrpy(x, y, z, roll, pitch, yaw, degrees=True, device="cuda"):
    if degrees:
        roll, pitch, yaw = np.radians([roll, pitch, yaw])
    Rx = np.array([[1, 0, 0],
                   [0, np.cos(roll), -np.sin(roll)],
                   [0, np.sin(roll), np.cos(roll)]])
    Ry = np.array([[np.cos(pitch), 0, np.sin(pitch)],
                   [0, 1, 0],
                   [-np.sin(pitch), 0, np.cos(pitch)]])
    Rz = np.array([[np.cos(yaw), -np.sin(yaw), 0],
                   [np.sin(yaw), np.cos(yaw), 0],
                   [0, 0, 1]])
    R = Rz @ Ry @ Rx
    T = np.array([x, y, z])
    viewmat = np.eye(4, dtype=np.float32)
    viewmat[:3, :3] = R
    viewmat[:3, 3] = T
    return torch.tensor(viewmat, dtype=torch.float32, device=device)

def render_frame(pose, H=512, W=512, fov=60.0):
    intrinsics = {
        "fov_x": torch.tensor([np.radians(fov)], device=device),
        "fov_y": torch.tensor([np.radians(fov)], device=device),
    }
    img = rasterization(
        means=gaussians["positions"],
        scales=gaussians["scales"],
        rotations=gaussians["rotations"],
        colors=gaussians["colors"],
        opacities=gaussians["opacities"],
        camera_pose=pose[None, :, :],
        **intrinsics,
        image_height=H,
        image_width=W,
    )
    return img[0].clamp(0, 1).cpu().numpy()

## Axis rotation

In [43]:
def euler_rotation_matrix(axis: str, angle_deg: float) -> np.ndarray:
    """Return a 3×3 rotation matrix for given axis and angle (degrees)."""
    angle = np.radians(angle_deg)
    c, s = np.cos(angle), np.sin(angle)
    if axis == "roll":   # x-axis
        R = np.array([[1, 0, 0],
                      [0, c, -s],
                      [0, s,  c]])
    elif axis == "pitch":  # y-axis
        R = np.array([[ c, 0, s],
                      [ 0, 1, 0],
                      [-s, 0, c]])
    elif axis == "yaw":  # z-axis
        R = np.array([[ c, -s, 0],
                      [ s,  c, 0],
                      [ 0,  0, 1]])
    else:
        raise ValueError(f"Unknown axis: {axis}")
    return R.astype(np.float32)


In [44]:
def rotate_camera_in_place(base_viewmat: torch.Tensor,
                           axis: str = "yaw",
                           total_angle: float = 360.0,
                           n_frames: int = 60) -> torch.Tensor:
    """
    Rotate the camera around its own center (spin in place).
    - Keeps camera position fixed
    - Rotates its local orientation around specified axis ('roll', 'pitch', 'yaw')
    """
    device = base_viewmat.device
    base_viewmat = base_viewmat.clone().cpu().numpy()
    base_R = base_viewmat[:3, :3]
    base_T = base_viewmat[:3, 3]

    poses = []
    for i in range(n_frames):
        angle = total_angle * i / n_frames
        R_delta = euler_rotation_matrix(axis, angle)
        R_new = R_delta @ base_R
        view = np.eye(4, dtype=np.float32)
        view[:3, :3] = R_new
        view[:3, 3] = base_T
        poses.append(torch.tensor(view, dtype=torch.float32, device=device))
    return torch.stack(poses)

## Orbit Rotation

In [45]:
def orbit_camera_around_center(center=(0, 0, 0),
                               radius: float = 2.0,
                               pitch: float = -30.0,
                               n_frames: int = 60,
                               device: str = "cuda") -> torch.Tensor:
    """
    Create camera poses orbiting around a given world center.
    - Camera always looks at the center
    - Moves on a circle of given radius
    - Pitch controls vertical tilt (in degrees)
    """
    cx, cy, cz = center
    up = np.array([0.0, 1.0, 0.0], dtype=np.float32)
    poses = []

    for i in range(n_frames):
        theta = 2 * np.pi * i / n_frames  # full 360°
        x = cx + radius * np.sin(theta)
        y = cy + radius * np.sin(np.radians(pitch))
        z = cz + radius * np.cos(theta)
        eye = np.array([x, y, z], dtype=np.float32)
        f = (np.array(center, dtype=np.float32) - eye)
        f /= np.linalg.norm(f)
        r = np.cross(f, up)
        r /= np.linalg.norm(r)
        u = np.cross(r, f)
        R = np.stack([r, u, -f], axis=1)
        view = np.eye(4, dtype=np.float32)
        view[:3, :3] = R
        view[:3, 3] = eye
        poses.append(torch.tensor(view, dtype=torch.float32, device=device))
    return torch.stack(poses)

In [ ]:
# If compiling for the first time
# !mkdir -p /content/drive/MyDrive/torch_extensions_cache
# !cp -r ~/.cache/torch_extensions/* /content/drive/MyDrive/torch_extensions_cache/
# print("Cached CUDA extensions to Drive.")

# Rendering

The following chapter demonstrates rendering of a scene:

### Configuration

In [66]:
NUM_FRAMES = 480
CENTER = (0.0, 1.0, 0.0) # around which point to rotate
ROTATION = (0.0, 0.0, 0.0)

## Rendering Yaw Rotation

The following method can be used to define a single view:

In [67]:
base_viewmat = pose_from_xyzrpy(*CENTER, *ROTATION)

Let's define a camera rotation around the point (note that the order of coordinates is ($x$, $z$, $y$):

In [68]:
# viewmats = rotate_camera_pose(base_viewmat, n_frames=NUM_FRAMES)
viewmats = orbit_camera_around_center((0.0, 1.0, 0.0), radius=1.0, pitch=0.0, n_frames=NUM_FRAMES)
print(viewmats.shape)

torch.Size([480, 4, 4])


This code is the main method for rendering a sequence of frames.



> **Please note that if you run rendering code for the first time, you should start it and interrupt immediately since it works indefinitely from the beginning. All further calls will work correctly without need to interrupt**



In [69]:
W, H = 640, 640
K = make_K(W, H)

frames = []
num_frames = NUM_FRAMES

for i, viewmat in enumerate(viewmats):

    img = rasterization(
        means=gaussians["means"],
        quats=gaussians["quats"],
        scales=gaussians["scales"],
        opacities=gaussians["opacities"],
        colors=gaussians["colors"],
        viewmats=viewmat[None],
        Ks=K[None],
        width=W,
        height=H,
        render_mode="RGB",
        rasterize_mode="classic"
    )

    frames.append(img[0].clamp(0, 1)[0].cpu().numpy())
    if i % 20 == 0:
        print(f"Rendered frame {i}/{num_frames}")

print("Rendering done!")

Rendered frame 0/480
Rendered frame 20/480
Rendered frame 40/480
Rendered frame 60/480
Rendered frame 80/480
Rendered frame 100/480
Rendered frame 120/480
Rendered frame 140/480
Rendered frame 160/480
Rendered frame 180/480
Rendered frame 200/480
Rendered frame 220/480
Rendered frame 240/480
Rendered frame 260/480
Rendered frame 280/480
Rendered frame 300/480
Rendered frame 320/480
Rendered frame 340/480
Rendered frame 360/480
Rendered frame 380/480
Rendered frame 400/480
Rendered frame 420/480
Rendered frame 440/480
Rendered frame 460/480
Rendering done!


Now, render frames using `mediapy` library and save the file locally:

In [70]:
media.write_video("orbit.mp4", frames, fps=30)
print("Saved video as orbit.mp4")
media.show_video(frames, fps=30)

Saved video as orbit.mp4


This browser does not support the video tag.


# Object Detection

Let's load an image box detection model and run it on the video frames:

## Loading YOLO-v5

In [ ]:
!pip install -U ultralytics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 41.8 MB/s eta 0:00:00


In [ ]:
from ultralytics import YOLO

# load a pre-trained or custom-trained model
model = YOLO('yolov5n.pt', verbose=False)

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.
PRO TIP 💡 Replace 'model=yolov5n.pt' with new 'model=yolov5nu.pt'.
YOLOv5 'u' models are trained with https://github.com/ultralytics/ultralytics and feature improved performance vs standard YOLOv5 models trained with https://github.com/ultralytics/yolov5.



In [ ]:
detection_frames = []

for frame in frames:
    new_frame = model(frame)[0].plot()
    detection_frames.append(new_frame)

In [ ]:
# media.write_video("detected.mp4", detection_frames, fps=30)
# print("Saved video as detected.mp4")
media.show_video(detection_frames, fps=30)

This browser does not support the video tag.


# Exploration

This chapter showcases methods for constructing a path to follow on a scene.

## 1. Voxel Grid

To start with, define a 3D view of the point cloud with spatial information - _voxel grid_

In [46]:
import numpy as np
import torch

def build_voxel_grid(points, voxel_size=0.1):
    """
    Build a voxel occupancy grid from 3D points.

    Args:
        points (torch.Tensor): [N, 3] tensor of xyz points.
        voxel_size (float): voxel edge length in world units.

    Returns:
        occupancy (np.ndarray): 3D boolean grid, True = occupied voxel
        origin (np.ndarray): world coords of voxel (0,0,0) corner
        voxel_size (float)
        bounds (tuple): (min_xyz, max_xyz)
    """

    # Convert to numpy
    pts = points.detach().cpu().numpy()   # [N, 3]

    # Compute bounding box
    min_xyz = pts.min(axis=0)
    max_xyz = pts.max(axis=0)
    bounds = (min_xyz, max_xyz)

    # Add small padding to avoid boundary issues
    padding = voxel_size * 2
    min_xyz -= padding
    max_xyz += padding

    # Compute grid resolution
    dims = ((max_xyz - min_xyz) / voxel_size).astype(int) + 1
    nx, ny, nz = dims

    print(f"Voxel grid dims: {nx} × {ny} × {nz}, total voxels={nx*ny*nz:,}")

    # Allocate occupancy grid
    occupancy = np.zeros((nx, ny, nz), dtype=bool)

    # Convert world coords → voxel indices
    voxel_indices = ((pts - min_xyz) / voxel_size).astype(int)

    # Clamp to avoid edge errors
    voxel_indices = np.clip(voxel_indices, 0, dims - 1)

    # Mark occupied voxels
    occupancy[voxel_indices[:, 0],
              voxel_indices[:, 1],
              voxel_indices[:, 2]] = True

    return occupancy, min_xyz, voxel_size, bounds

In [47]:
gaussians = load_gaussian_ply(PLY_PATH)
points = gaussians["means"]   # [N, 3]

occupancy, origin, vox_size, bounds = build_voxel_grid(points, voxel_size=0.1)

print("Origin:", origin)
print("Voxel size:", vox_size)
print("Bounds:", bounds)

Voxel grid dims: 9600 × 9081 × 9459, total voxels=824,612,918,400
Origin: [-483.63864 -423.95218 -457.76028]
Voxel size: 0.1
Bounds: (array([-483.63864, -423.95218, -457.76028], dtype=float32), array([476.3267 , 484.08838, 488.0588 ], dtype=float32))


## 2. Sampling

I employ random sampling of points in the free space of the voxel grid with a pruning mechanism to avoid overlap

In [48]:
def random_sample_world(bounds, n_samples):
    """
    Sample random world coordinates inside bounding box.
    bounds = (min_xyz, max_xyz)
    """
    min_xyz, max_xyz = bounds
    return np.random.uniform(min_xyz, max_xyz, size=(n_samples, 3))

In [49]:
def is_voxel_safe(occupancy, v, clearance=2):
    """
    Check if voxel v = (i, j, k) is free and has clearance.
    Fast: checks only a tiny neighborhood.
    """
    x, y, z = v
    nx, ny, nz = occupancy.shape

    # Check inside bounds
    if x < 0 or x >= nx or y < 0 or y >= ny or z < 0 or z >= nz:
        return False

    # Must be free
    if occupancy[x, y, z]:
        return False

    # Check neighbors for clearance
    x0 = max(0, x - clearance)
    x1 = min(nx, x + clearance + 1)
    y0 = max(0, y - clearance)
    y1 = min(ny, y + clearance + 1)
    z0 = max(0, z - clearance)
    z1 = min(nz, z + clearance + 1)

    region = occupancy[x0:x1, y0:y1, z0:z1]
    return not region.any()    # True if no obstacles nearby

In [50]:
def filter_random_samples(world_pts, origin, voxel_size, occupancy, clearance=2):
    safe_points = []
    safe_voxels = []

    for p in world_pts:
        v = ((p - origin) / voxel_size).astype(int)
        if is_voxel_safe(occupancy, tuple(v), clearance=clearance):
            safe_points.append(p)
            safe_voxels.append(v)

    return np.array(safe_points), np.array(safe_voxels)

In [51]:
def poisson_prune(points, min_dist):
    if len(points) == 0:
        return points

    selected = []
    pts = points.copy()
    np.random.shuffle(pts)
    min_dist2 = min_dist * min_dist

    for p in pts:
        if not selected:
            selected.append(p)
        else:
            d2 = np.sum((np.array(selected) - p)**2, axis=1)
            if np.min(d2) >= min_dist2:
                selected.append(p)

    return np.array(selected)

In [52]:
N = 10  # number of random samples to try

# 1. Generate random world samples
sub_bounds = [
    np.array([0, 0.2, 0], dtype=np.float32),
    np.array([3, 4, 3], dtype=np.float32)
]
rand_pts = random_sample_world(sub_bounds, N)

# 2. Filter samples using local clearance check
camera_pts, voxels = filter_random_samples(
    rand_pts,
    origin=origin,
    voxel_size=vox_size,
    occupancy=occupancy,
    clearance=3
)

print("Safe camera points:", len(camera_pts))

# 3. Optional: thin set
camera_pts = poisson_prune(camera_pts, min_dist=0.5)

print("Final camera samples:", len(camera_pts))

Safe camera points: 6
Final camera samples: 5


## 3.  Path Planning

Since we sampled several points, A* can interconnect them into a single path avoiding obstacles

### __A*__ path finding

In [53]:
import heapq
import numpy as np

# 6-connected by default; use 26 for diagonal moves
NEIGHBORS_6 = [
    (1,0,0), (-1,0,0),
    (0,1,0), (0,-1,0),
    (0,0,1), (0,0,-1)
]

def astar_voxel(start, goal, occupancy):
    """
    A* on a 3D voxel grid.

    - start, goal: integer voxel indices (ix, iy, iz)
    - occupancy: boolean 3D array, True = occupied, False = free
    """
    sx, sy, sz = start
    gx, gy, gz = goal

    def heuristic(i, j, k):
        return ((i-gx)**2 + (j-gy)**2 + (k-gz)**2)**0.5

    # Min-heap priority queue
    open_set = []
    heapq.heappush(open_set, (0, start))

    came_from = {}
    g_cost = {start: 0}
    f_cost = {start: heuristic(*start)}

    visited = set()

    while open_set:
        _, current = heapq.heappop(open_set)

        if current in visited:
            continue
        visited.add(current)

        if current == goal:
            # Reconstruct path
            path = [current]
            while current in came_from:
                current = came_from[current]
                path.append(current)
            return path[::-1]

        cx, cy, cz = current

        # Explore neighbors
        for dx, dy, dz in NEIGHBORS_6:
            nx, ny, nz = cx + dx, cy + dy, cz + dz

            # Bounds check
            if (nx < 0 or ny < 0 or nz < 0 or
                nx >= occupancy.shape[0] or
                ny >= occupancy.shape[1] or
                nz >= occupancy.shape[2]):
                continue

            # Skip obstacles
            if occupancy[nx, ny, nz]:
                continue

            neighbor = (nx, ny, nz)
            tentative_g = g_cost[current] + 1  # cost 1 per step

            if tentative_g < g_cost.get(neighbor, float('inf')):
                came_from[neighbor] = current
                g_cost[neighbor] = tentative_g
                f_cost[neighbor] = tentative_g + heuristic(nx, ny, nz)
                heapq.heappush(open_set, (f_cost[neighbor], neighbor))

    return None  # No path found

In [54]:
def world_to_voxel(p, origin, voxel_size):
    return tuple(((p - origin) / voxel_size).astype(int))

def voxel_to_world(v, origin, voxel_size):
    return origin + np.array(v) * voxel_size

Let's demonstrate a path between the first and the second points:

In [ ]:
start_world = camera_pts[0]
goal_world  = camera_pts[1]

start_voxel = world_to_voxel(start_world, origin, vox_size)
goal_voxel  = world_to_voxel(goal_world, origin, vox_size)

path_voxels = astar_voxel(start_voxel, goal_voxel, occupancy)

# Convert to world coordinates
path_world = [voxel_to_world(v, origin, vox_size) for v in path_voxels]

In [ ]:
path = [start_world] + path_world + [goal_world]

In [ ]:
W, H = 256, 256
K = make_K(W, H)

frames = []

for i, pos in enumerate(path):

    viewmat = pose_from_xyzrpy(
        pos[0], pos[1], pos[2],
        0, 0, 0
    )

    img = rasterization(
        means=gaussians["means"],
        quats=gaussians["quats"],
        scales=gaussians["scales"],
        opacities=gaussians["opacities"],
        colors=gaussians["colors"],
        viewmats=viewmat[None],
        Ks=K[None],
        width=W,
        height=H,
        render_mode="RGB",
        rasterize_mode="classic"
    )

    frames.append(img[0].clamp(0, 1)[0].cpu().numpy())
    if i % 20 == 0:
        print(f"Rendered frame {i}")

print("Rendering done!")

Rendered frame 0
Rendered frame 20
Rendering done!


In [ ]:
# media.write_video("sample_path.mp4", frames, fps=30)
# print("Saved video as sample_path.mp4")
media.show_video(frames, fps=30)

This browser does not support the video tag.


### Connecting Sampled Points into Single Path

In [55]:
import numpy as np
from sklearn.neighbors import NearestNeighbors

def plan_visit_order_and_path(start_world,
                              targets_world,
                              occupancy,
                              origin,
                              voxel_size,
                              k=10):
    """
    Given:
        start_world   : (3,) float world coordinate
        targets_world : (N,3) float array of world coordinates to visit
        occupancy     : 3D boolean array, True=occupied, False=free
        origin        : world coordinate of voxel grid origin
        voxel_size    : float voxel size
        k             : number of nearest candidate points to consider

    Returns:
        visit_order   : list of indices of targets in the visiting order
        full_path_world : list of world coordinates forming the complete A* path
    """

    # Convert all points to voxel indices
    start_voxel = world_to_voxel(start_world, origin, voxel_size)
    target_voxels = np.array(
        [world_to_voxel(p, origin, voxel_size) for p in targets_world],
        dtype=int
    )

    # Keep track of unvisited indices
    remaining = set(range(len(targets_world)))
    visit_order = []
    full_path_world = []

    # Current position (voxel and world)
    current_voxel = start_voxel
    full_path_world.append(start_world)

    # Build KD-tree for nearest-neighbor queries
    nbrs = NearestNeighbors(n_neighbors=min(k, len(targets_world)),
                            algorithm='kd_tree')
    nbrs.fit(targets_world)

    while remaining:
        # Query k nearest unvisited targets in world space
        distances, indices = nbrs.kneighbors([voxel_to_world(current_voxel, origin, voxel_size)],
                                             n_neighbors=min(k, len(remaining)))
        candidate_indices = [idx for idx in indices[0] if idx in remaining]

        best_candidate = None
        best_path = None
        best_length = float("inf")

        # Try A* to each candidate
        for ci in candidate_indices:
            goal_voxel = tuple(target_voxels[ci])
            path_voxels = astar_voxel(tuple(current_voxel), goal_voxel, occupancy)

            if path_voxels is None:
                continue  # unreachable target

            path_length = len(path_voxels)
            if path_length < best_length:
                best_length = path_length
                best_candidate = ci
                best_path = path_voxels

        # If none of the k-nearest is reachable, fallback to brute-search
        if best_candidate is None:
            for ci in list(remaining):
                goal_voxel = tuple(target_voxels[ci])
                path_voxels = astar_voxel(tuple(current_voxel), goal_voxel, occupancy)
                if path_voxels is None:
                    continue
                path_length = len(path_voxels)
                if path_length < best_length:
                    best_length = path_length
                    best_candidate = ci
                    best_path = path_voxels

        # If still unreachable (scene disconnected)
        if best_candidate is None:
            print("Warning: some targets unreachable from current position.")
            break

        # Add candidate to visit order
        visit_order.append(best_candidate)
        remaining.remove(best_candidate)

        # Convert best_path voxels to world and append to full trajectory
        for v in best_path[1:]:  # skip first point (same as last of previous)
            full_path_world.append(voxel_to_world(np.array(v), origin, voxel_size))

        # Update current point
        current_voxel = tuple(target_voxels[best_candidate])

    return visit_order, np.array(full_path_world)

In [56]:
start = camera_pts[0]
targets = camera_pts  # (N,3) array
visit_order, full_path = plan_visit_order_and_path(
    start_world=start,
    targets_world=targets,
    occupancy=occupancy,
    origin=origin,
    voxel_size=vox_size,
    k=3,
)

print("Visit order:", visit_order)
print("Total path length:", len(full_path))

Visit order: [np.int64(0), np.int64(4), np.int64(1), np.int64(2), 3]
Total path length: 89


In [ ]:
W, H = 256, 256
K = make_K(W, H)

frames = []

for i, pos in enumerate(full_path):

    viewmat = pose_from_xyzrpy(
        pos[0], pos[1], pos[2],
        0, 0, 0
    )

    img = rasterization(
        means=gaussians["means"],
        quats=gaussians["quats"],
        scales=gaussians["scales"],
        opacities=gaussians["opacities"],
        colors=gaussians["colors"],
        viewmats=viewmat[None],
        Ks=K[None],
        width=W,
        height=H,
        render_mode="RGB",
        rasterize_mode="classic"
    )

    frames.append(img[0].clamp(0, 1)[0].cpu().numpy())
    if i % 20 == 0:
        print(f"Rendered frame {i}")

print("Rendering done!")

Rendered frame 0
Rendered frame 20
Rendered frame 40
Rendered frame 60
Rendered frame 80
Rendered frame 100
Rendered frame 120
Rendered frame 140
Rendered frame 160
Rendered frame 180
Rendered frame 200
Rendering done!


In [ ]:
# media.write_video("full_path.mp4", frames, fps=30)
# print("Saved video as full_path.mp4")
media.show_video(frames, fps=30)

This browser does not support the video tag.


## 5. Trajectory Planning

To make the camera movements more smooth, let's apply Hermite cubic interpolation

In [57]:
import numpy as np

def _normalize(v, eps=1e-9):
    n = np.linalg.norm(v)
    if n < eps:
        return v
    return v / n

def mat_to_quat(R):
    """
    Convert 3x3 rotation matrix to quaternion (w, x, y, z).
    Stable numerics.
    """
    M = np.asarray(R, dtype=float)
    trace = M[0,0] + M[1,1] + M[2,2]
    if trace > 0:
        s = 0.5 / np.sqrt(trace + 1.0)
        w = 0.25 / s
        x = (M[2,1] - M[1,2]) * s
        y = (M[0,2] - M[2,0]) * s
        z = (M[1,0] - M[0,1]) * s
    else:
        # find largest diagonal element
        if M[0,0] > M[1,1] and M[0,0] > M[2,2]:
            s = 2.0 * np.sqrt(1.0 + M[0,0] - M[1,1] - M[2,2])
            w = (M[2,1] - M[1,2]) / s
            x = 0.25 * s
            y = (M[0,1] + M[1,0]) / s
            z = (M[0,2] + M[2,0]) / s
        elif M[1,1] > M[2,2]:
            s = 2.0 * np.sqrt(1.0 + M[1,1] - M[0,0] - M[2,2])
            w = (M[0,2] - M[2,0]) / s
            x = (M[0,1] + M[1,0]) / s
            y = 0.25 * s
            z = (M[1,2] + M[2,1]) / s
        else:
            s = 2.0 * np.sqrt(1.0 + M[2,2] - M[0,0] - M[1,1])
            w = (M[1,0] - M[0,1]) / s
            x = (M[0,2] + M[2,0]) / s
            y = (M[1,2] + M[2,1]) / s
            z = 0.25 * s
    q = np.array([w, x, y, z], dtype=float)
    return q / np.linalg.norm(q)

def quat_slerp(q0, q1, t):
    """
    Spherical linear interpolation between quaternions q0,q1 (w,x,y,z) at t in [0,1].
    """
    q0 = q0 / np.linalg.norm(q0)
    q1 = q1 / np.linalg.norm(q1)
    dot = np.dot(q0, q1)
    if dot < 0.0:
        q1 = -q1
        dot = -dot
    DOT_THRESHOLD = 0.9995
    if dot > DOT_THRESHOLD:
        # Linear fallback
        res = q0 + t*(q1 - q0)
        return res / np.linalg.norm(res)
    theta_0 = np.arccos(dot)
    theta = theta_0 * t
    q2 = q1 - q0 * dot
    q2 = q2 / np.linalg.norm(q2)
    return (np.cos(theta) * q0) + (np.sin(theta) * q2)

In [58]:
def smooth_path_with_camera_orientations(path_points,
                                         samples_per_segment=20,
                                         up=np.array([0.0, 1.0, 0.0]),
                                         keep_roll=0.0):
    """
    Smooth a discrete path (Nx3) using cubic Hermite (Catmull-Rom tangents),
    sample it densely, and produce camera orientations that smoothly follow the path.

    Args:
        path_points: (N,3) array-like of waypoints (N >= 2).
        samples_per_segment: int, number of output samples per input segment.
        up: world up-vector (3,), used as a reference for orientation.
        keep_roll: optional roll angle (radians) applied around forward axis.

    Returns:
        positions: (M,3) numpy array of sampled positions along the smooth spline.
        quaternions: (M,4) numpy array of orientations (w,x,y,z) where the camera
                     looks along the -Z camera axis and X is to the right.
    Notes:
        - This uses Catmull-Rom style tangents: m_i = 0.5*(p_{i+1} - p_{i-1}).
        - End tangents are set to difference to neighbor (p1-p0, pN-1-pN-2).
        - Orientations are constructed so forward = normalized velocity vector.
    """
    pts = np.asarray(path_points, dtype=float)
    if pts.ndim != 2 or pts.shape[1] != 3:
        raise ValueError("path_points must be (N,3)")
    N = len(pts)
    if N < 2:
        raise ValueError("Need at least 2 points in path_points")

    # Build tangents (Catmull-Rom-style)
    tangents = np.zeros_like(pts)
    if N == 2:
        tangents[0] = (pts[1] - pts[0])
        tangents[1] = (pts[1] - pts[0])
    else:
        # interior
        for i in range(1, N-1):
            tangents[i] = 0.5 * (pts[i+1] - pts[i-1])
        # endpoints
        tangents[0] = pts[1] - pts[0]
        tangents[-1] = pts[-1] - pts[-2]

    # Hermite basis functions (for s in [0,1])
    def hermite_pos(p0, p1, m0, m1, s):
        s2 = s*s
        s3 = s2*s
        h00 =  2*s3 - 3*s2 + 1
        h10 =      s3 - 2*s2 + s
        h01 = -2*s3 + 3*s2
        h11 =      s3 -   s2
        return (h00[:,None]*p0 +
                h10[:,None]*m0 +
                h01[:,None]*p1 +
                h11[:,None]*m1)

    def hermite_derivative(p0, p1, m0, m1, s):
        # derivative w.r.t s (s in [0,1])
        s2 = s*s
        dh00 = 6*s2 - 6*s
        dh10 = 3*s2 - 4*s + 1
        dh01 = -6*s2 + 6*s
        dh11 = 3*s2 - 2*s
        return (dh00[:,None]*p0 +
                dh10[:,None]*m0 +
                dh01[:,None]*p1 +
                dh11[:,None]*m1)

    # Sample segments
    positions = []
    orientations = []

    eps = 1e-8
    prev_forward = None
    for i in range(N-1):
        p0 = pts[i]
        p1 = pts[i+1]
        m0 = tangents[i]
        m1 = tangents[i+1]

        # build sample s values for this segment
        # exclude the last sample (it becomes the first of next segment), except for final segment
        if i < N-2:
            s_vals = np.linspace(0.0, 1.0, samples_per_segment, endpoint=False)
        else:
            # include endpoint of final segment
            s_vals = np.linspace(0.0, 1.0, samples_per_segment, endpoint=True)

        s_vals = np.asarray(s_vals, dtype=float)
        if s_vals.size == 0:
            continue

        # compute positions
        p_samples = hermite_pos(np.repeat(p0[None,:], len(s_vals), axis=0),
                                np.repeat(p1[None,:], len(s_vals), axis=0),
                                np.repeat(m0[None,:], len(s_vals), axis=0),
                                np.repeat(m1[None,:], len(s_vals), axis=0),
                                s_vals)
        # compute derivative (tangent) w.r.t param s
        dp_ds = hermite_derivative(np.repeat(p0[None,:], len(s_vals), axis=0),
                                   np.repeat(p1[None,:], len(s_vals), axis=0),
                                   np.repeat(m0[None,:], len(s_vals), axis=0),
                                   np.repeat(m1[None,:], len(s_vals), axis=0),
                                   s_vals)

        for idx in range(len(s_vals)):
            pos = p_samples[idx]
            vel = dp_ds[idx]
            # If velocity tiny, fallback to next/previous segment direction
            if np.linalg.norm(vel) < 1e-6:
                if prev_forward is not None:
                    forward = prev_forward
                else:
                    # fallback: use segment direction
                    d = p1 - p0
                    forward = _normalize(d) if np.linalg.norm(d) > eps else np.array([0,0,-1.0])
            else:
                forward = _normalize(vel)

            # Ensure forward is not parallel to up; if so, pick a different up
            up_vec = np.asarray(up, dtype=float)
            if abs(np.dot(forward, _normalize(up_vec))) > 0.999:
                # forward almost parallel to up -> pick arbitrary orthogonal up
                up_vec = np.array([1.0, 0.0, 0.0], dtype=float)

            right = _normalize(np.cross(up_vec, forward))
            # guard against zero right
            if np.linalg.norm(right) < 1e-6:
                right = np.array([1.0, 0.0, 0.0])
            up_corrected = _normalize(np.cross(forward, right))

            # Build rotation matrix R = [right, up_corrected, -forward] as columns
            R = np.column_stack([right, up_corrected, -forward])

            # apply optional roll about forward axis
            if abs(keep_roll) > 1e-9:
                # rotate R by angle keep_roll around forward axis
                ca = np.cos(keep_roll); sa = np.sin(keep_roll)
                # rotation in camera local x-y plane (around -Z camera axis)
                # construct roll matrix in camera frame and apply
                roll_mat_cam = np.array([[ca, -sa, 0],
                                         [sa,  ca, 0],
                                         [0,   0,  1]], dtype=float)
                R = R @ roll_mat_cam  # rotate columns appropriately

            q = mat_to_quat(R)
            positions.append(pos)
            orientations.append(q)
            prev_forward = forward

    positions = np.asarray(positions, dtype=float)
    quaternions = np.asarray(orientations, dtype=float)

    return positions, quaternions

In [59]:
pos, quats = smooth_path_with_camera_orientations(full_path, samples_per_segment=30)
print("sampled positions:", pos.shape)
print("sampled quaternions:", quats.shape)

sampled positions: (2640, 3)
sampled quaternions: (2640, 4)


In [ ]:
W, H = 256, 256
K = make_K(W, H)

frames = []

for i in range(pos.shape[0]):

    pos_i = pos[i]

    viewmat = pose_from_xyzrpy(
        pos_i[0], pos_i[1], pos_i[2],
        0, 0, 0
    )

    img = rasterization(
        means=gaussians["means"],
        quats=gaussians["quats"],
        scales=gaussians["scales"],
        opacities=gaussians["opacities"],
        colors=gaussians["colors"],
        viewmats=viewmat[None],
        Ks=K[None],
        width=W,
        height=H,
        render_mode="RGB",
        rasterize_mode="classic"
    )

    frames.append(img[0].clamp(0, 1)[0].cpu().numpy())
    if i % 20 == 0:
        print(f"Rendered frame {i}")

print("Rendering done!")

In [62]:
media.show_video(frames, fps=30)

This browser does not support the video tag.
